VedEf Operating Window Problem Setup.

This module provides the canonical Problem instance for the VedEf operating
window example. All analysis and optimization scripts should import and use
setup_vedef_problem() to ensure consistency.


In [ ]:
import importlib.util
from pathlib import Path

import openmdao.api as om


def setup_vedef_problem(target_power=25000.0, max_energy_density=1e9, as_subsystem=True):
    """Set up VedEf OpenMDAO problem with default parameter values.

    Parameters
    ----------
    target_power : float, optional
        Target total power in W. Default: 25000.0 (25 kW)
    max_energy_density : float, optional
        Maximum arc energy density in J/m^3. Default: 1e9 (1 GJ/m^3)
    as_subsystem : bool, optional
        If True, adds VedEfDesignGroup as a subsystem (hierarchical).
        If False, uses VedEfDesignGroup directly as the model. Default: True

    Returns
    -------
    openmdao.api.Problem
        Configured problem ready for optimization/analysis with:
        - VedEfDesignGroup configured with specified parameters
        - Default parameter values set
        - Problem setup() called

    Examples
    --------
    >>> prob = setup_vedef_problem()
    >>> prob.run_model()
    >>> print(prob.get_val("T_0"))
    """
    # Import VedEfDesignGroup from the model definition file
    spec = importlib.util.spec_from_file_location(
        "vedef_module", Path(__file__).parent / "1_model_vedef_design_group.py"
    )
    vedef_module = importlib.util.module_from_spec(spec)
    spec.loader.exec_module(vedef_module)
    VedEfDesignGroup = vedef_module.VedEfDesignGroup

    prob = om.Problem()
    vedef_group = VedEfDesignGroup(target_power=target_power, max_energy_density=max_energy_density)

    if as_subsystem:
        prob.model.add_subsystem("vedef", vedef_group, promotes=["*"])
    else:
        prob.model = vedef_group

    # Setup the problem
    prob.setup()

    # Set default values (using ARC002 parameter tags)
    prob.set_val("G_UMAX_OUT", 20000.0, units="V")  # Generator voltage
    prob.set_val("G_e", 0.01, units="m")  # Interelectrode gap
    prob.set_val("TP_D_OUT", 0.02, units="m")  # Torch outlet diameter
    prob.set_val("G_F", 50000.0, units="Hz")  # PRF - Pulse Frequency
    prob.set_val("G_Ep", 0.01, units="J")  # Energy per pulse

    return prob